# Requirements to collpase requirements tables Note + Making Concordances Concord - Tony Gui

In [1]:
import pandas as pd
import numpy as np
from dotenv import dotenv_values, find_dotenv
import os
import re
from data_cleaning_functions import requirements_clean, concordance_PCE_clean, \
    find_intermediate_industries, concordance_PCQ_clean, get_sales_from_make_matrix, clean_make_matrix
from pathlib import Path
import warnings
warnings.filterwarnings('ignore', category=FutureWarning, message=".*concatenation with empty or all-NA entries is deprecated.*")

script_dir = str(Path().resolve().parent)
file_path = os.path.join(script_dir) + "\\" 
Shapiro_data =  file_path + "shapiro_data"
raw_data_path = file_path + "raw_bea_data" 

# 1. Load in Requirements Matrix 

In [2]:
requirements = pd.read_excel(os.path.join(raw_data_path, 'CxC_TR_2017_PRO_DET.xlsx'), sheet_name='2017')
requirements = requirements_clean(requirements)
requirements

2                                                oilseed farming  \
nan                                                                
oilseed farming                                         1.279503   
grain farming                                           0.001994   
vegetable and melon farming                             0.000014   
fruit and tree nut farming                              0.000032   
greenhouse, nursery, and floriculture production         0.00056   
...                                                          ...   
other state and local government enterprises            0.000822   
scrap                                                   0.000929   
used and secondhand goods                               0.000698   
noncomparable imports                                   0.006582   
rest of the world adjustment                                   0   

2                                                grain farming  \
nan                                                              
oilseed farming                                       0.013426   
grain farming                                         1.158617   
vegetable and melon farming                           0.000038   
fruit and tree nut farming                            0.000068   
greenhouse, nursery, and floriculture production       0.00162   
...                                                        ...   
other state and local government enterprises          0.001584   
scrap                                                 0.001912   
used and secondhand goods                             0.001076   
noncomparable imports                                 0.013388   
rest of the world adjustment                                 0   

2                                                vegetable and melon farming  \
nan                                                                            
oilseed farming                                                     0.004149   
grain farming                                                       0.003495   
vegetable and melon farming                                         1.036742   
fruit and tree nut farming                                          0.000046   
greenhouse, nursery, and floriculture production                    0.001217   
...                                                                      ...   
other state and local government enterprises                        0.001165   
scrap                                                                0.00125   
used and secondhand goods                                           0.000899   
noncomparable imports                                               0.003879   
rest of the world adjustment                                               0   

2                                                fruit and tree nut farming  \
nan                                                                           
oilseed farming                                                    0.000968   
grain farming                                                      0.002679   
vegetable and melon farming                                          0.0001   
fruit and tree nut farming                                          1.02564   
greenhouse, nursery, and floriculture production                   0.000939   
...                                                                     ...   
other state and local government enterprises                       0.000707   
scrap                                                              0.000746   
used and secondhand goods                                          0.000578   
noncomparable imports                                              0.002506   
rest of the world adjustment                                              0   

2                                                greenhouse, nursery, and floriculture production  \
nan                                                                                   

# 2. Calculate Delta

In [3]:
requirements = requirements.T
with pd.option_context("future.no_silent_downcasting", True):
    requirements = requirements.fillna(0).infer_objects(copy=False)
delta = np.identity(len(requirements)) - np.linalg.inv(requirements)
delta = pd.DataFrame(delta, index=requirements.index, columns=requirements.columns)
delta

nan                                               oilseed farming  \
2                                                                   
oilseed farming                                      2.180219e-01   
grain farming                                        7.868216e-03   
vegetable and melon farming                          2.138190e-03   
fruit and tree nut farming                          -9.282810e-09   
greenhouse, nursery, and floriculture production    -2.546387e-09   
...                                                           ...   
other state and local government enterprises        -5.212040e-08   
scrap                                               -3.231149e-08   
used and secondhand goods                            0.000000e+00   
noncomparable imports                                0.000000e+00   
rest of the world adjustment                        -6.531900e-04   

nan                                               grain farming  \
2                                                                 
oilseed farming                                    3.257965e-08   
grain farming                                      1.329214e-01   
vegetable and melon farming                       -4.288926e-09   
fruit and tree nut farming                         5.073217e-08   
greenhouse, nursery, and floriculture production   4.003457e-08   
...                                                         ...   
other state and local government enterprises      -1.483361e-08   
scrap                                              2.454273e-05   
used and secondhand goods                          0.000000e+00   
noncomparable imports                              0.000000e+00   
rest of the world adjustment                      -8.977927e-05   

nan                                               vegetable and melon farming  \
2                                                                               
oilseed farming                                                  1.901259e-08   
grain farming                                                    1.348177e-08   
vegetable and melon farming                                      3.541394e-02   
fruit and tree nut farming                                       7.026986e-05   
greenhouse, nursery, and floriculture production                 1.041431e-08   
...                                                                       ...   
other state and local government enterprises                    -1.885922e-08   
scrap                                                            1.120530e-05   
used and secondhand goods                                        0.000000e+00   
noncomparable imports                                            0.000000e+00   
rest of the world adjustment                                    -1.424104e-08   

nan                                               fruit and tree nut farming  \
2                                                                              
oilseed farming                                                -2.337597e-08   
grain farming                                                   2.867714e-08   
vegetable and melon farming                                    -1.698949e-08   
fruit and tree nut farming                                      2.496465e-02   
greenhouse, nursery, and floriculture production               -5.650610e-09   
...                                                                      ...   
other state and local government enterprises                    4.340038e-09   
scrap                                                           4.363264e-05   
used and secondhand goods                                       0.000000e+00   
noncomparable imports                                           0.000000e+00   
rest of the world adjustment                                   -1.723238e-08   

nan                                               greenhouse, nursery, and floriculture production  \
2                                

# 2.5b Making Negative Values in Delta Zero

In [4]:
negative_count = (delta < 0).sum().sum()
x = negative_count/402**2
delta[delta < 0] = 0
negative_count_new = (delta < 0).sum().sum()
y = negative_count_new/402**2

# 2.5b Force negatives to be zero but adjust row sums to be same as before

In [5]:
# V = delta.sum(axis=0)
# P = delta[delta > 0].sum()
# delta.loc['norm'] = V/P
# last_values = delta.iloc[-1]
# delta[delta < 0] = 0
# delta = delta.iloc[:-1].div(last_values)
# delta

# Dealting with Intermediate Industries - Making Concordances Concord Section 3.3.1. - Operationalizing Industries without Products

# Step 1. Making Concordances Concord

In [6]:
use_table = pd.read_excel(os.path.join(raw_data_path, "Use_SUT_Framework_2017_DET.xlsx"), sheet_name="2017")
# Returns all industries with zero PCE 
intermediate_industries = find_intermediate_industries(use_table)

intermediate_industries = intermediate_industries.iloc[:, [0]]
intermediate_industries = intermediate_industries.sort_values(by="Industry")
intermediate_industries

Industry
106               air and gas compressor manufacturing
163     aircraft engine and engine parts manufacturing
67          all other forging, stamping, and sintering
344  all other miscellaneous professional, scientif...
291                                   all other retail
..                                                 ...
81              valve and fittings other than plumbing
42   veneer, plywood, and engineered wood product m...
281  wholesale electronic markets and agents and br...
145                        wiring device manufacturing
173  wood kitchen cabinet and countertop manufacturing

[143 rows x 1 columns]

# Steps 2 - 5. Making Concordances Concord - Loop over Intermediate Industries and Remove

In [7]:
# For the Loop 
big_lambda = np.eye(len(delta)) # create a big_lambda identity matrix that will become our final output
big_lambda = pd.DataFrame(big_lambda)
big_lambda = big_lambda.set_index(delta.index)
big_lambda.columns = delta.index
delta_industries = delta.index # save all the requirment table industries outside the loop 
removed = [] # stores all removed industries through the loop 

i = 0
for row in intermediate_industries.iloc[::-1].itertuples(): # looping backwards
    i += 1 
    current = row.Industry # industry we are currently removing
    # Create identity matrix for current loop iteration
    phi_i = np.eye(len(delta) - (i - 1))
    phi_i = pd.DataFrame(phi_i)
    phi_i = phi_i.set_index(delta_industries)
    phi_i.columns = delta_industries

    current_intermediate_use_table = delta.copy() # use a new intermediates use matrix each time we do this
    current_intermediate_use_table.drop(columns=removed, inplace=True) # Remove all the industries we've previously removed in earlier loop iterations 
    current_intermediate_use_table = current_intermediate_use_table.loc[[current]] # the row of the intermediates use table associated with the current industry  
    current_intermediate_use_table.drop(columns=[current], inplace=True) # drop the column associated with the current industry so we dont include it in our sum
    current_intermediate_use_table = current_intermediate_use_table.astype(float)
    current_industry_sum = current_intermediate_use_table.loc[current].sum() # find sum of row

    # just making sure that we aren't dividing by zero 
    if current_industry_sum != 0:
        current_intermediate_use_table = current_intermediate_use_table.astype(float)
        current_intermediate_use_table.loc[current] = current_intermediate_use_table.loc[current] / current_industry_sum

    current_intermediate_use_table = current_intermediate_use_table[sorted(current_intermediate_use_table.columns)] # sort the normazlied row alphabetically

    # remove the current industry from intermediate list
    intermediate_industries = intermediate_industries[intermediate_industries['Industry'] != current]
    # drop the current industry column from phi_i and industry indexing
    phi_i = phi_i.drop(columns=current)
    delta_industries = delta_industries.drop(current) 
    
    removed.append(current)

    # Update phi_i with the current industry sale shares
    phi_i.loc[current_intermediate_use_table.index] = current_intermediate_use_table.loc[current_intermediate_use_table.index].astype(np.float64).values
    big_lambda_old = big_lambda
    big_lambda = big_lambda @ phi_i

In [8]:
big_lambda

2                                                 grain farming  \
2                                                                 
oilseed farming                                        0.000342   
grain farming                                          1.000000   
vegetable and melon farming                            0.000000   
fruit and tree nut farming                             0.000000   
greenhouse, nursery, and floriculture production       0.000000   
...                                                         ...   
other state and local government enterprises           0.000000   
scrap                                                  0.000000   
used and secondhand goods                              0.000000   
noncomparable imports                                  0.000000   
rest of the world adjustment                           0.000000   

2                                                 vegetable and melon farming  \
2                                                                               
oilseed farming                                                      0.000177   
grain farming                                                        0.000000   
vegetable and melon farming                                          1.000000   
fruit and tree nut farming                                           0.000000   
greenhouse, nursery, and floriculture production                     0.000000   
...                                                                       ...   
other state and local government enterprises                         0.000000   
scrap                                                                0.000000   
used and secondhand goods                                            0.000000   
noncomparable imports                                                0.000000   
rest of the world adjustment                                         0.000000   

2                                                 fruit and tree nut farming  \
2                                                                              
oilseed farming                                                     0.015147   
grain farming                                                       0.000000   
vegetable and melon farming                                         0.000000   
fruit and tree nut farming                                          1.000000   
greenhouse, nursery, and floriculture production                    0.000000   
...                                                                      ...   
other state and local government enterprises                        0.000000   
scrap                                                               0.000000   
used and secondhand goods                                           0.000000   
noncomparable imports                                               0.000000   
rest of the world adjustment                                        0.000000   

2                                                 greenhouse, nursery, and floriculture production  \
2                                                                                                    
oilseed farming                                                                           0.000898   
grain farming                                                                             0.000000   
vegetable and melon farming                                                               0.000000   
fruit and tree nut farming                                                                0.000000   
greenhouse, nursery, and floriculture production                                          1.000000   
...                                                                                            ...   
other state and local government enterprises                                              0.000000   
scrap                                                                                     0.000000   
used and seco

# Step 6. Making Concordances Concord - Converting IO matrix from sales shares to dollars

In [9]:
make_matrix = pd.read_excel(os.path.join(raw_data_path, "Supply_2017_DET.xlsx"), sheet_name="2017")
sales_vector = get_sales_from_make_matrix(make_matrix) # returns the sales for each industry

# repeat the sales vector n times to make a sales matrix
sales_repeated = pd.DataFrame({f'{i}': sales_vector['Sales'].values for i in range(1, len(delta))})
sales_matrix = pd.concat([sales_vector, sales_repeated], axis=1)
sales_matrix = sales_matrix.set_index(sales_matrix.columns[0])
sales_matrix.columns = delta.columns

# Y is IO matrix in dollars 
Y = delta * sales_matrix 
Y

nan                                               oilseed farming  \
2                                                                   
oilseed farming                                       8267.827572   
grain farming                                          525.518137   
vegetable and melon farming                             39.731851   
fruit and tree nut farming                               0.000000   
greenhouse, nursery, and floriculture production         0.000000   
...                                                           ...   
other state and local government enterprises             0.000000   
scrap                                                    0.000000   
used and secondhand goods                                0.000000   
noncomparable imports                                    0.000000   
rest of the world adjustment                             0.000000   

nan                                               grain farming  \
2                                                                 
oilseed farming                                        0.001235   
grain farming                                       8877.820655   
vegetable and melon farming                            0.000000   
fruit and tree nut farming                             0.001508   
greenhouse, nursery, and floriculture production       0.000795   
...                                                         ...   
other state and local government enterprises           0.000000   
scrap                                                  0.264153   
used and secondhand goods                              0.000000   
noncomparable imports                                  0.000000   
rest of the world adjustment                           0.000000   

nan                                               vegetable and melon farming  \
2                                                                               
oilseed farming                                                      0.000721   
grain farming                                                        0.000900   
vegetable and melon farming                                        658.061803   
fruit and tree nut farming                                           2.089193   
greenhouse, nursery, and floriculture production                     0.000207   
...                                                                       ...   
other state and local government enterprises                         0.000000   
scrap                                                                0.120603   
used and secondhand goods                                            0.000000   
noncomparable imports                                                0.000000   
rest of the world adjustment                                         0.000000   

nan                                               fruit and tree nut farming  \
2                                                                              
oilseed farming                                                     0.000000   
grain farming                                                       0.001915   
vegetable and melon farming                                         0.000000   
fruit and tree nut farming                                        742.224105   
greenhouse, nursery, and floriculture production                    0.000000   
...                                                                      ...   
other state and local government enterprises                        0.000465   
scrap                                                               0.469618   
used and secondhand goods                                           0.000000   
noncomparable imports                                               0.000000   
rest of the world adjustment                                        0.000000   

nan                                               greenhouse, nursery, and floriculture production  \
2                                

# Step 7. Making Concordances Concord - Value Added for the Economy

In [10]:
sum_Y = Y.sum(axis=1).to_frame()
sum_Y.columns = ['Sales']
sum_Y.index.name = "Industries"
sales_vector = sales_vector.set_index(sales_vector.columns[0])

VA_pre_transformation = (sales_vector - sum_Y).sum()
VA_pre_transformation = VA_pre_transformation.Sales

# Step 8. Making Concordances Concord - IO Matrix in USD

In [11]:
# new IO matrix in USD 
Y_tilde = big_lambda.T @ Y @ big_lambda
sales_tilde = big_lambda.T @ sales_vector

# Verifing that economy wide value added is identical to the pre-transformation level
sum_Y_tilde = Y_tilde.sum(axis=1).to_frame()
sum_Y_tilde.columns = ['Sales']
VA_post_transformation = (sales_tilde - sum_Y_tilde).sum()
VA_post_transformation = VA_post_transformation.Sales

In [12]:
differnece = VA_post_transformation - VA_pre_transformation
differnece

-925.2822083681822

# Step 9. Making Concordances Concord - Calculating New Delta

In [13]:
recip_sales = 1/sales_tilde
sales_tilde_repeated = pd.DataFrame({f'{i}': recip_sales['Sales'].values for i in range(1, len(delta))})
sales_tilde_repeated.set_index(recip_sales.index, inplace=True)
sales_tilde_matrix = pd.concat([recip_sales, sales_tilde_repeated], axis=1)
sales_tilde_matrix.columns = delta.columns

delta_tilde = Y_tilde * sales_tilde_matrix
delta = delta_tilde
delta

abrasive product manufacturing  \
2                                                                                  
grain farming                                                           0.001855   
vegetable and melon farming                                             0.001475   
fruit and tree nut farming                                              0.001449   
greenhouse, nursery, and floriculture production                        0.001765   
other crop farming                                                      0.001552   
...                                                                          ...   
other state and local government enterprises                            0.001345   
scrap                                                                   0.009547   
used and secondhand goods                                               0.002826   
noncomparable imports                                                   0.001199   
rest of the world adjustment                                            0.001072   

                                                  accommodation  \
2                                                                 
grain farming                                          0.001159   
vegetable and melon farming                            0.003187   
fruit and tree nut farming                             0.001760   
greenhouse, nursery, and floriculture production       0.001233   
other crop farming                                     0.001739   
...                                                         ...   
other state and local government enterprises           0.000997   
scrap                                                  0.001566   
used and secondhand goods                              0.002404   
noncomparable imports                                  0.001560   
rest of the world adjustment                           0.002145   

                                                  accounting, tax preparation, bookkeeping, and payroll services  \
2                                                                                                                  
grain farming                                                                              0.003837                
vegetable and melon farming                                                                0.005865                
fruit and tree nut farming                                                                 0.007114                
greenhouse, nursery, and floriculture production                                           0.006487                
other crop farming                                                                         0.006864                
...                                                                                             ...                
other state and local government enterprises                                               0.006144                
scrap                                                                                      0.004104                
used and secondhand goods                                                                  0.005590                
noncomparable imports                                                                      0.004433                
rest of the world adjustment                                                               0.004530                

                                                  adhesive manufacturing  \
2                                                                          
grain farming                                                   0.000749   
vegetable and melon farming                                     0.000667   
fruit and tree nut farming                                      0.000871   
greenhouse, nursery, and floriculture production                0.000889   
other crop farming                                              0.000708   
...                                         

# End of Making Concordances Concord - Back to Requirements to Collapse Requirements Table

# 3. Merge Concordance with Delta

In [14]:
concordance = pd.read_excel(os.path.join(raw_data_path, "PCEBridge_2017_DET.xlsx"), sheet_name="2017")
concordance = concordance_PCE_clean(concordance)
concordance

PCE Bridge Products  \
4                                   new domestic autos   
5                                   new domestic autos   
6                                    new foreign autos   
7                                     new light trucks   
8                                           used autos   
..                                                 ...   
702  final consumption expenditures of nonprofit in...   
703  final consumption expenditures of nonprofit in...   
704  final consumption expenditures of nonprofit in...   
705  final consumption expenditures of nonprofit in...   
706  final consumption expenditures of nonprofit in...   

                                 PCE Bridge Industries  
4                             automobile manufacturing  
5                     motor vehicle body manufacturing  
6                             automobile manufacturing  
7        light truck and utility vehicle manufacturing  
8                                                scrap  
..                                                 ...  
702         museums, historical sites, zoos, and parks  
703          other amusement and recreation industries  
704                            religious organizations  
705  grantmaking, giving, and social advocacy organ...  
706  civic, social, professional, and similar organ...  

[703 rows x 2 columns]

In [15]:
"""the problem here is some industries in the requirments matrix still have no match to PCE they are matching to PEQ so i must drop them here when im trying to 
make the requirments table in terms of products however im not sure if this changes some of the math performed to the requirments matrix ie delta later on"""
industries_in_requirments = set(delta.columns)
indsutries_in_concordance = set(concordance["PCE Bridge Industries"])
industires_not_in_concordance = industries_in_requirments - indsutries_in_concordance
delta = delta.drop(index=industires_not_in_concordance, columns=industires_not_in_concordance, errors='ignore')
delta

abrasive product manufacturing  \
2                                                                                  
grain farming                                                           0.001855   
vegetable and melon farming                                             0.001475   
fruit and tree nut farming                                              0.001449   
greenhouse, nursery, and floriculture production                        0.001765   
other crop farming                                                      0.001552   
...                                                                          ...   
other state and local government enterprises                            0.001345   
scrap                                                                   0.009547   
used and secondhand goods                                               0.002826   
noncomparable imports                                                   0.001199   
rest of the world adjustment                                            0.001072   

                                                  accommodation  \
2                                                                 
grain farming                                          0.001159   
vegetable and melon farming                            0.003187   
fruit and tree nut farming                             0.001760   
greenhouse, nursery, and floriculture production       0.001233   
other crop farming                                     0.001739   
...                                                         ...   
other state and local government enterprises           0.000997   
scrap                                                  0.001566   
used and secondhand goods                              0.002404   
noncomparable imports                                  0.001560   
rest of the world adjustment                           0.002145   

                                                  accounting, tax preparation, bookkeeping, and payroll services  \
2                                                                                                                  
grain farming                                                                              0.003837                
vegetable and melon farming                                                                0.005865                
fruit and tree nut farming                                                                 0.007114                
greenhouse, nursery, and floriculture production                                           0.006487                
other crop farming                                                                         0.006864                
...                                                                                             ...                
other state and local government enterprises                                               0.006144                
scrap                                                                                      0.004104                
used and secondhand goods                                                                  0.005590                
noncomparable imports                                                                      0.004433                
rest of the world adjustment                                                               0.004530                

                                                  adhesive manufacturing  \
2                                                                          
grain farming                                                   0.000749   
vegetable and melon farming                                     0.000667   
fruit and tree nut farming                                      0.000871   
greenhouse, nursery, and floriculture production                0.000889   
other crop farming                                              0.000708   
...                                         

In [16]:
in_num_products = concordance['PCE Bridge Industries'].value_counts()

delta_product_columns = pd.DataFrame(index=delta.index, columns=concordance['PCE Bridge Products'])

for column in delta_product_columns: 
    industry = concordance.loc[concordance['PCE Bridge Products'] == column, 'PCE Bridge Industries'].values
    delta_product_columns[column] = delta[industry] / in_num_products[industry]

delta_product_cr = pd.DataFrame(columns=delta_product_columns.columns)
lst_for_industry = []
for row in delta_product_columns.index:
    final_value = delta_product_columns.loc[row] / in_num_products[row]
    products = concordance[concordance['PCE Bridge Industries'] == row]['PCE Bridge Products'].tolist()
    for product in products: 
        lst_for_industry.append(row)
        final_value_row = pd.DataFrame(final_value).T
        final_value_row.index = [product]
        
        delta_product_cr = pd.concat([delta_product_cr, final_value_row])

industry = pd.DataFrame(lst_for_industry, columns=['industry'])
industry.index = delta_product_cr.index
delta_product_cr = pd.concat([delta_product_cr, industry], axis = 1)
delta_product_cr

new domestic autos  \
cereals                                                       0.000021   
processed fruits and vegetables                               0.000021   
pets and related products                                     0.000021   
food furnished to employees (including military)              0.000021   
vegetables (fresh)                                            0.000030   
...                                                                ...   
private employees' expenditures abroad                        0.000019   
u.s. travel outside the united states                         0.000019   
u.s. student expenditures                                     0.000019   
less: personal remittances in kind to nonresidents            0.000051   
less: expenditures in the united states by nonr...            0.000051   

                                                    new domestic autos  \
cereals                                                       0.000070   
processed fruits and vegetables                               0.000070   
pets and related products                                     0.000070   
food furnished to employees (including military)              0.000070   
vegetables (fresh)                                            0.000195   
...                                                                ...   
private employees' expenditures abroad                        0.000184   
u.s. travel outside the united states                         0.000184   
u.s. student expenditures                                     0.000184   
less: personal remittances in kind to nonresidents            0.000425   
less: expenditures in the united states by nonr...            0.000425   

                                                    new foreign autos  \
cereals                                                      0.000021   
processed fruits and vegetables                              0.000021   
pets and related products                                    0.000021   
food furnished to employees (including military)             0.000021   
vegetables (fresh)                                           0.000030   
...                                                               ...   
private employees' expenditures abroad                       0.000019   
u.s. travel outside the united states                        0.000019   
u.s. student expenditures                                    0.000019   
less: personal remittances in kind to nonresidents           0.000051   
less: expenditures in the united states by nonr...           0.000051   

                                                    new light trucks  \
cereals                                                     0.000224   
processed fruits and vegetables                             0.000224   
pets and related products                                   0.000224   
food furnished to employees (including military)            0.000224   
vegetables (fresh)                                          0.000131   
...                                                              ...   
private employees' expenditures abroad                      0.000060   
u.s. travel outside the united states                       0.000060   
u.s. student expenditures                                   0.000060   
less: personal remittances in kind to nonresidents          0.000133   
less: expenditures in the united states by nonr...          0.000133   

                                                    used autos    used autos  \
cereals                                               0.000029  3.548166e-07   
processed fruits and vegetables                       0.000029  3.548166e-07   
pets and related products                             0.000029  3.548166e-07   
food furnished to employees (including military)      0.000029  3.548166e-07   
vegetables (fresh)                                    0.000021  1.382115e-06   
...                                                 

# 4. Collapse columns

In [17]:
delta_products = delta_product_cr.T.groupby(delta_product_cr.columns).sum().T
delta_products

accessories and parts  \
cereals                                                         0.002733   
processed fruits and vegetables                                 0.002733   
pets and related products                                       0.002733   
food furnished to employees (including military)                0.002733   
vegetables (fresh)                                                 0.003   
...                                                                  ...   
private employees' expenditures abroad                          0.002172   
u.s. travel outside the united states                           0.002172   
u.s. student expenditures                                       0.002172   
less: personal remittances in kind to nonresidents              0.005146   
less: expenditures in the united states by nonr...              0.005146   

                                                   air transportation  \
cereals                                                      0.000096   
processed fruits and vegetables                              0.000096   
pets and related products                                    0.000096   
food furnished to employees (including military)             0.000096   
vegetables (fresh)                                           0.000291   
...                                                               ...   
private employees' expenditures abroad                       0.000132   
u.s. travel outside the united states                        0.000132   
u.s. student expenditures                                    0.000132   
less: personal remittances in kind to nonresidents           0.000448   
less: expenditures in the united states by nonr...           0.000448   

                                                   alcohol in purchased meals  \
cereals                                                              0.001424   
processed fruits and vegetables                                      0.001424   
pets and related products                                            0.001424   
food furnished to employees (including military)                     0.001424   
vegetables (fresh)                                                   0.001584   
...                                                                       ...   
private employees' expenditures abroad                               0.000803   
u.s. travel outside the united states                                0.000803   
u.s. student expenditures                                            0.000803   
less: personal remittances in kind to nonresidents                   0.001971   
less: expenditures in the united states by nonr...                   0.001971   

                                                   all other professional medical services  \
cereals                                                                           0.000101   
processed fruits and vegetables                                                   0.000101   
pets and related products                                                         0.000101   
food furnished to employees (including military)                                  0.000101   
vegetables (fresh)                                                                 0.00012   
...                                                                                    ...   
private employees' expenditures abroad                                            0.000116   
u.s. travel outside the united states                                             0.000116   
u.s. student expenditures                                                         0.000116   
less: personal remittances in kind to nonresidents                                0.000223   
less: expenditures in the united states by nonr...                                0.000223   

                                                   amusement parks, campgrounds, and related recreational services  \
cereals                                  

# 5. Make Matrix to Sales

In [18]:
make_matrix = pd.read_excel(os.path.join(raw_data_path, "Supply_2017_DET.xlsx"), sheet_name='2017')
sales = get_sales_from_make_matrix(make_matrix)
sales

3                                          Industries   Sales
0                                     oilseed farming   37922
1                                       grain farming   66790
2                         vegetable and melon farming   18582
3                          fruit and tree nut farming   29731
4    greenhouse, nursery, and floriculture production   19868
..                                                ...     ...
397      other state and local government enterprises  107059
398                                             scrap   10763
399                         used and secondhand goods       0
400                             noncomparable imports       0
401                      rest of the world adjustment    3468

[402 rows x 2 columns]

# 6. Merge concordance with sales 

In [19]:
product_sales = pd.merge(concordance, sales, left_on='PCE Bridge Industries', right_on='Industries')
product_sales = product_sales[["PCE Bridge Products", "Industries", 'Sales']]
product_sales

PCE Bridge Products  \
0                                   new domestic autos   
1                                   new domestic autos   
2                                    new foreign autos   
3                                     new light trucks   
4                                           used autos   
..                                                 ...   
698  final consumption expenditures of nonprofit in...   
699  final consumption expenditures of nonprofit in...   
700  final consumption expenditures of nonprofit in...   
701  final consumption expenditures of nonprofit in...   
702  final consumption expenditures of nonprofit in...   

                                            Industries   Sales  
0                             automobile manufacturing   32758  
1                     motor vehicle body manufacturing   10556  
2                             automobile manufacturing   32758  
3        light truck and utility vehicle manufacturing  215421  
4                                                scrap   10763  
..                                                 ...     ...  
698         museums, historical sites, zoos, and parks   20894  
699          other amusement and recreation industries   81734  
700                            religious organizations  100202  
701  grantmaking, giving, and social advocacy organ...   58458  
702  civic, social, professional, and similar organ...   95191  

[703 rows x 3 columns]

# 7. Group sum of Sales for every Product

In [20]:
# calculates the number of product categories an Industry belongs to 
product_sales['In#Products'] = product_sales['Industries'].map(product_sales['Industries'].value_counts())
product_sales["Ratio_in_Product"] = product_sales['Sales'] / product_sales['In#Products'] 
product_sales['Sales_Sum'] = product_sales.groupby('PCE Bridge Products')['Ratio_in_Product'].transform('sum')
product_sales

PCE Bridge Products  \
0                                   new domestic autos   
1                                   new domestic autos   
2                                    new foreign autos   
3                                     new light trucks   
4                                           used autos   
..                                                 ...   
698  final consumption expenditures of nonprofit in...   
699  final consumption expenditures of nonprofit in...   
700  final consumption expenditures of nonprofit in...   
701  final consumption expenditures of nonprofit in...   
702  final consumption expenditures of nonprofit in...   

                                            Industries   Sales  In#Products  \
0                             automobile manufacturing   32758            2   
1                     motor vehicle body manufacturing   10556            1   
2                             automobile manufacturing   32758            2   
3        light truck and utility vehicle manufacturing  215421            1   
4                                                scrap   10763            6   
..                                                 ...     ...          ...   
698         museums, historical sites, zoos, and parks   20894            3   
699          other amusement and recreation industries   81734            3   
700                            religious organizations  100202            2   
701  grantmaking, giving, and social advocacy organ...   58458            3   
702  civic, social, professional, and similar organ...   95191            4   

     Ratio_in_Product     Sales_Sum  
0        16379.000000  2.693500e+04  
1        10556.000000  2.693500e+04  
2        16379.000000  1.637900e+04  
3       215421.000000  2.154210e+05  
4         1793.833333  1.793833e+03  
..                ...           ...  
698       6964.666667  1.554667e+06  
699      27244.666667  1.554667e+06  
700      50101.000000  1.554667e+06  
701      19486.000000  1.554667e+06  
702      23797.750000  1.554667e+06  

[703 rows x 6 columns]

# 8. Sales Share 

In [21]:
product_sales['Sale Share'] = product_sales["Ratio_in_Product"] / product_sales["Sales_Sum"]
product_sales = product_sales.rename(columns={'Industries': 'industry'})
product_sales = product_sales.rename(columns={'PCE Bridge Products': 'product'})
product_sales

product  \
0                                   new domestic autos   
1                                   new domestic autos   
2                                    new foreign autos   
3                                     new light trucks   
4                                           used autos   
..                                                 ...   
698  final consumption expenditures of nonprofit in...   
699  final consumption expenditures of nonprofit in...   
700  final consumption expenditures of nonprofit in...   
701  final consumption expenditures of nonprofit in...   
702  final consumption expenditures of nonprofit in...   

                                              industry   Sales  In#Products  \
0                             automobile manufacturing   32758            2   
1                     motor vehicle body manufacturing   10556            1   
2                             automobile manufacturing   32758            2   
3        light truck and utility vehicle manufacturing  215421            1   
4                                                scrap   10763            6   
..                                                 ...     ...          ...   
698         museums, historical sites, zoos, and parks   20894            3   
699          other amusement and recreation industries   81734            3   
700                            religious organizations  100202            2   
701  grantmaking, giving, and social advocacy organ...   58458            3   
702  civic, social, professional, and similar organ...   95191            4   

     Ratio_in_Product     Sales_Sum  Sale Share  
0        16379.000000  2.693500e+04    0.608094  
1        10556.000000  2.693500e+04    0.391906  
2        16379.000000  1.637900e+04    1.000000  
3       215421.000000  2.154210e+05    1.000000  
4         1793.833333  1.793833e+03    1.000000  
..                ...           ...         ...  
698       6964.666667  1.554667e+06    0.004480  
699      27244.666667  1.554667e+06    0.017524  
700      50101.000000  1.554667e+06    0.032226  
701      19486.000000  1.554667e+06    0.012534  
702      23797.750000  1.554667e+06    0.015307  

[703 rows x 7 columns]

# 9. Merge Sale shares and Delta

In [22]:
df_reset = delta_products.reset_index()
delta_products = df_reset.rename(columns={'index': 'product'})
delta_products_saleshare = delta_products.merge(product_sales, how = 'inner', on = ['industry', 'product'])
delta_products_saleshare = delta_products_saleshare.drop(columns=['Sales_Sum', "Ratio_in_Product", "In#Products", "Sales", "industry"])
delta_products_saleshare = delta_products_saleshare.set_index(delta_products_saleshare.columns[0])
delta_products_saleshare

accessories and parts  \
product                                                                    
cereals                                                         0.002733   
processed fruits and vegetables                                 0.002733   
pets and related products                                       0.002733   
food furnished to employees (including military)                0.002733   
vegetables (fresh)                                                 0.003   
...                                                                  ...   
private employees' expenditures abroad                          0.002172   
u.s. travel outside the united states                           0.002172   
u.s. student expenditures                                       0.002172   
less: personal remittances in kind to nonresidents              0.005146   
less: expenditures in the united states by nonr...              0.005146   

                                                   air transportation  \
product                                                                 
cereals                                                      0.000096   
processed fruits and vegetables                              0.000096   
pets and related products                                    0.000096   
food furnished to employees (including military)             0.000096   
vegetables (fresh)                                           0.000291   
...                                                               ...   
private employees' expenditures abroad                       0.000132   
u.s. travel outside the united states                        0.000132   
u.s. student expenditures                                    0.000132   
less: personal remittances in kind to nonresidents           0.000448   
less: expenditures in the united states by nonr...           0.000448   

                                                   alcohol in purchased meals  \
product                                                                         
cereals                                                              0.001424   
processed fruits and vegetables                                      0.001424   
pets and related products                                            0.001424   
food furnished to employees (including military)                     0.001424   
vegetables (fresh)                                                   0.001584   
...                                                                       ...   
private employees' expenditures abroad                               0.000803   
u.s. travel outside the united states                                0.000803   
u.s. student expenditures                                            0.000803   
less: personal remittances in kind to nonresidents                   0.001971   
less: expenditures in the united states by nonr...                   0.001971   

                                                   all other professional medical services  \
product                                                                                      
cereals                                                                           0.000101   
processed fruits and vegetables                                                   0.000101   
pets and related products                                                         0.000101   
food furnished to employees (including military)                                  0.000101   
vegetables (fresh)                                                                 0.00012   
...                                                                                    ...   
private employees' expenditures abroad                                            0.000116   
u.s. travel outside the united states                                             0.000116   
u.s. student expenditures                                                         0.000116   
less: personal remittanc

# 10. weightTimesDeltaValue + 11.

In [23]:
# Convert from Wide to Long
delta_final = delta_products_saleshare.reset_index().melt(id_vars=[delta_products_saleshare.index.name, "Sale Share"],
                                var_name="Column Products", value_name="value")

# Just Renaming and Reordering
delta_final = delta_final.rename(columns={delta_products_saleshare.index.name: "Row Products"})
delta_final = delta_final[['Row Products', 'Column Products', 'value', 'Sale Share']]
# Calculating weightTimesDeltaValue
delta_final["weightTimesDeltaValue"] = delta_final["value"] * delta_final["Sale Share"]

# Sum weightTimesDeltaValue grouping by Row Products AND Column Products
delta_final = delta_final.groupby(['Row Products', 'Column Products']).sum()
delta_final
# Convert Back to Wide Format 
delta_final = delta_final.pivot_table(values='weightTimesDeltaValue', index='Row Products', columns='Column Products')

# Removes Index and Column Names cuz it looks better. Both Index and Columns are simply Product Categories now
delta_final.columns.name = None 
delta_final.index.name = None 
delta_final

accessories and parts  \
accessories and parts                                            0.09031   
air transportation                                              0.000792   
alcohol in purchased meals                                      0.002152   
all other professional medical services                         0.001599   
amusement parks, campgrounds, and related recre...              0.003414   
...                                                                  ...   
water transportation                                             0.00403   
window coverings                                                0.006544   
wine                                                            0.015671   
women's and girls' clothing                                     0.002761   
workers' compensation                                           0.000557   

                                                   air transportation  \
accessories and parts                                        0.000485   
air transportation                                           0.000058   
alcohol in purchased meals                                   0.000155   
all other professional medical services                      0.000127   
amusement parks, campgrounds, and related recre...           0.000267   
...                                                               ...   
water transportation                                         0.000384   
window coverings                                             0.000134   
wine                                                         0.000384   
women's and girls' clothing                                  0.000098   
workers' compensation                                        0.000026   

                                                   alcohol in purchased meals  \
accessories and parts                                                0.003131   
air transportation                                                    0.00108   
alcohol in purchased meals                                           0.001818   
all other professional medical services                              0.002809   
amusement parks, campgrounds, and related recre...                    0.00169   
...                                                                       ...   
water transportation                                                 0.001177   
window coverings                                                     0.000858   
wine                                                                 0.002442   
women's and girls' clothing                                          0.000705   
workers' compensation                                                0.000565   

                                                   all other professional medical services  \
accessories and parts                                                             0.000357   
air transportation                                                                 0.00002   
alcohol in purchased meals                                                        0.000091   
all other professional medical services                                           0.000249   
amusement parks, campgrounds, and related recre...                                0.000152   
...                                                                                    ...   
water transportation                                                              0.000107   
window coverings                                                                  0.000119   
wine                                                                              0.000271   
women's and girls' clothing                                                       0.000078   
workers' compensation                                                             0.000025   

                                                   amusement parks, campgrounds, and related recreational services  \
accessories and parts                    

# 12. Calculate Gamma

In [24]:
row_sums = delta_final.sum(axis=1)
gamma = pd.DataFrame(row_sums, columns=['Row_Sum'])
gamma.index = delta_final.index 
gamma

Row_Sum
accessories and parts                               0.495184
air transportation                                  0.074848
alcohol in purchased meals                          0.159275
all other professional medical services             0.104428
amusement parks, campgrounds, and related recre...  0.152453
...                                                      ...
water transportation                                0.163773
window coverings                                    0.148454
wine                                                0.554591
women's and girls' clothing                          0.08931
workers' compensation                               0.078006

[212 rows x 1 columns]

# 13. Calculate Omega

In [25]:
delta_gamma = delta_final.merge(gamma, left_on=gamma.index, right_on=delta_final.index)
delta_gamma = delta_gamma.set_index(delta_gamma.columns[0])
row_sums = delta_gamma.iloc[:, -1]
row_sums[row_sums == 0] = np.nan
omega = delta_gamma.iloc[:, :-1].div(row_sums, axis=0)
omega.columns.name = None 
omega.index.name = None 
omega

accessories and parts  \
accessories and parts                                           0.182376   
air transportation                                              0.010587   
alcohol in purchased meals                                      0.013513   
all other professional medical services                         0.015309   
amusement parks, campgrounds, and related recre...              0.022395   
...                                                                  ...   
water transportation                                            0.024607   
window coverings                                                 0.04408   
wine                                                            0.028258   
women's and girls' clothing                                     0.030914   
workers' compensation                                           0.007136   

                                                   air transportation  \
accessories and parts                                        0.000979   
air transportation                                           0.000777   
alcohol in purchased meals                                   0.000976   
all other professional medical services                      0.001215   
amusement parks, campgrounds, and related recre...            0.00175   
...                                                               ...   
water transportation                                         0.002343   
window coverings                                             0.000902   
wine                                                         0.000693   
women's and girls' clothing                                  0.001095   
workers' compensation                                        0.000331   

                                                   alcohol in purchased meals  \
accessories and parts                                                0.006322   
air transportation                                                   0.014429   
alcohol in purchased meals                                           0.011413   
all other professional medical services                              0.026902   
amusement parks, campgrounds, and related recre...                   0.011085   
...                                                                       ...   
water transportation                                                 0.007184   
window coverings                                                     0.005782   
wine                                                                 0.004403   
women's and girls' clothing                                          0.007889   
workers' compensation                                                0.007243   

                                                   all other professional medical services  \
accessories and parts                                                             0.000721   
air transportation                                                                0.000274   
alcohol in purchased meals                                                         0.00057   
all other professional medical services                                           0.002386   
amusement parks, campgrounds, and related recre...                                0.000995   
...                                                                                    ...   
water transportation                                                              0.000653   
window coverings                                                                  0.000802   
wine                                                                              0.000489   
women's and girls' clothing                                                       0.000877   
workers' compensation                                                             0.000322   

                                                   amusement parks, campgrounds, and related recreational services  \
accessories and parts                    

# Start of Doing our Supply/demand contribution graph properly (Which influenceer has hte most influence?)

In [26]:
shaprio_proucts = pd.read_excel(os.path.join(Shapiro_data, 'shaprio_products.xlsx'))
shaprio_proucts = shaprio_proucts["Products"].to_frame()
shaprio_proucts['Products'] = shaprio_proucts['Products'].apply(lambda x: re.sub(r'\([^\)]*\d[^\)]*\)', '', x))
shaprio_proucts['Products'] = shaprio_proucts['Products'].str.rstrip()
shaprio_proucts['Products'] = shaprio_proucts['Products'].str.lower()
shaprio_proucts

# gamma_shaprio = gamma[gamma["Unnamed: 0"].isin(shaprio_proucts['Products'])]
# gamma_shaprio.reset_index(drop=True, inplace=True)
# gamma_shaprio

Products
0                                            new autos
1                                     new light trucks
2                                           used autos
3                                    used light trucks
4                                                tires
..                                                 ...
125                     repair of household appliances
126                           other household services
127                   foreign travel by u.s. residents
128  less: expenditures in the united states by non...
129  final consumption expenditures of nonprofit in...

[130 rows x 1 columns]